### Hwo to run the code:
#### First, download the data and save in the path "./original_data/"
Download SQuAD(v1.1) from: https://deepai.org/dataset/squad  
Download GloVe(840B, 300d) from: https://github.com/stanfordnlp/GloVe
#### Second, run preprocess to get the train set and validation set
#### Third, run this jupyter notebook

#### Version
Python 3.9.7  
tensorflow 2.6.0

In [1]:
import os
import tensorflow as tf
import tensorflow_addons as tfa
import numpy as np
import pandas as pd
import pickle
import collections
from QANet import QANet
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import Callback
from utils.output import write_predictions
from utils.evaluation import evaluate
from params import Params

In [2]:
params = Params()
# load train data
with open("dataset/train_set.pkl", 'rb') as f:
    train_data = pickle.load(f)
train_data['start_label_fin'] = np.argmax(train_data['y_start'], axis=-1)
train_data['end_label_fin'] = np.argmax(train_data['y_end'], axis=-1)

# load validation data
with open("./dataset/dev_set.pkl", 'rb') as f:
    dev_data = pickle.load(f)
with open('./dataset/dev_examples.pkl', 'rb') as f:
    eval_examples = pickle.load(f)
with open('./dataset/dev_features.pkl', 'rb') as f:
    eval_features = pickle.load(f)

# load embedding matrix
word_mat = np.load('./dataset/word_emb_mat.npy')
char_mat = np.load('./dataset/char_emb_mat.npy')

ems = []
f1s = []
model = QANet(params, word_mat=word_mat, char_mat=char_mat)
optimizer = Adam(learning_rate=params.learning_rate, beta_1=0.8, beta_2=0.999, epsilon=1e-7, clipnorm=5.)
optimizer = tfa.optimizers.MovingAverage(optimizer, average_decay=0.9999)
model.compile(optimizer=optimizer, loss=['categorical_crossentropy', 'categorical_crossentropy', 'mae', 'mae'],
              loss_weights=[0.5, 0.5, 0, 0])
Result = collections.namedtuple("Result",
                                ["qid", "start_logits", "end_logits"])

In [3]:
class QANetCallback(Callback):
    def __init__(self):
        super(Callback, self).__init__()
        self.global_step = 1
        self.max_f1 = 0

    def on_train_begin(self, logs=None):
        learning_rate = min(params.learning_rate,
                            params.learning_rate / np.log(params.warm_up_steps) * np.log(self.global_step))
        tf.keras.backend.set_value(self.model.optimizer.learning_rate, learning_rate)

    def on_epoch_begin(self, epoch, logs=None):
        # use a list to store the loss of each epoch
        self.losses = []

    def on_batch_end(self, batch, logs=None):
        self.global_step += 1
        # the learning warm-up scheme
        learning_rate = min(params.learning_rate,
                            params.learning_rate / np.log(params.warm_up_steps) * np.log(self.global_step))
        tf.keras.backend.set_value(self.model.optimizer.learning_rate, learning_rate)
        loss = logs.get('loss')
        self.losses.append(loss)

    def on_epoch_end(self, epoch, logs=None):
        logits1, logits2, _, _ = self.model.predict(x=[dev_data['context_id'], dev_data['question_id'],
                                                       dev_data['context_char_id'], dev_data['question_char_id']],
                                                    batch_size=params.batch_size,
                                                    verbose=1)
        all_results = []
        for i, qid in enumerate(dev_data['qid']):
            start_logits = logits1[i, :]
            end_logits = logits2[i, :]
            all_results.append(Result(qid=qid,
                                      start_logits=start_logits,
                                      end_logits=end_logits))
        output_prediction_file = os.path.join('output_prediction.json')
        output_nbest_file = os.path.join('output_nbest.json')
        write_predictions(eval_examples, eval_features, all_results,
                          n_best_size=20, max_answer_length=params.ans_limit,
                          do_lower_case=False, output_prediction_file=output_prediction_file,
                          output_nbest_file=output_nbest_file)
        metrics = evaluate('original_data/dev-v1.1.json', output_prediction_file, None)
        ems.append(metrics['exact'])
        f1s.append(metrics['f1'])
        result = pd.DataFrame([ems, f1s], index=['em', 'f1']).transpose()
        result.to_csv('./logs/result.csv', index=False)
        # write the losses of each epoch
        with open("./logs/losses_epoch" + str(epoch) + ".txt", 'a', encoding='utf=8') as f:
            for loss in self.losses:
                f.write(str(loss) + '\n')
        if f1s[-1] > self.max_f1:
            self.max_f1 = f1s[-1]
            model.save_weights("./saved_model_epoch" + str(epoch) + "/QANet_model_epoch" + str(epoch) + ".tf")


In [4]:
qanet_callback = QANetCallback()
qanet_callback.set_model(model)
model.fit(x=[train_data['context_id'], train_data['question_id'],
             train_data['context_char_id'], train_data['question_char_id']],
          y=[train_data['y_start'], train_data['y_end'], train_data['start_label_fin'],
             train_data['end_label_fin']],
          batch_size=params.batch_size,
          epochs=params.epoch,
          callbacks=[qanet_callback])
model.summary()

E:\Anaconda3\envs\envTF26\lib\site-packages\tensorflow\python\data\ops\dataset_ops.py:4211: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  warnings.warn(


Epoch 1/2
  20/7312 [..............................] - ETA: 1:36:48 - loss: 13.6040 - output_1_loss: 13.0478 - output_2_loss: 14.1583 - output_3_loss: 56.9042 - output_4_loss: 50.5583WARNING:tensorflow:Gradients do not exist for variables ['qa_net/highway0_gate/bias:0', 'qa_net/highway0_linear/bias:0', 'qa_net/multi_head_attention/bias:0', 'qa_net/multi_head_attention_1/bias:0'] when minimizing the loss.


  41/7312 [..............................] - ETA: 1:32:03 - loss: 12.4948 - output_1_loss: 12.1408 - output_2_loss: 12.8470 - output_3_loss: 53.6443 - output_4_loss: 50.1280WARNING:tensorflow:Gradients do not exist for variables ['qa_net/highway0_gate/bias:0', 'qa_net/highway0_linear/bias:0', 'qa_net/multi_head_attention/bias:0', 'qa_net/multi_head_attention_1/bias:0'] when minimizing the loss.


  62/7312 [..............................] - ETA: 1:31:00 - loss: 11.2295 - output_1_loss: 10.8246 - output_2_loss: 11.6325 - output_3_loss: 51.8750 - output_4_loss: 49.5027WARNING:tensorflow:Gradients do not exist for variables ['qa_net/highway0_gate/bias:0', 'qa_net/highway0_linear/bias:0', 'qa_net/multi_head_attention/bias:0', 'qa_net/multi_head_attention_1/bias:0'] when minimizing the loss.


  83/7312 [..............................] - ETA: 1:30:18 - loss: 10.1027 - output_1_loss: 9.7556 - output_2_loss: 10.4480 - output_3_loss: 51.4839 - output_4_loss: 49.7269WARNING:tensorflow:Gradients do not exist for variables ['qa_net/highway0_gate/bias:0', 'qa_net/highway0_linear/bias:0', 'qa_net/multi_head_attention/bias:0', 'qa_net/multi_head_attention_1/bias:0'] when minimizing the loss.


...

7285/7312 [============================>.] - ETA: 17s - loss: 2.9589 - output_1_loss: 3.0486 - output_2_loss: 2.8653 - output_3_loss: 32.2661 - output_4_loss: 32.2525WARNING:tensorflow:Gradients do not exist for variables ['qa_net/highway0_gate/bias:0', 'qa_net/highway0_linear/bias:0', 'qa_net/multi_head_attention/bias:0', 'qa_net/multi_head_attention_1/bias:0'] when minimizing the loss.


7306/7312 [============================>.] - ETA: 3s - loss: 2.9592 - output_1_loss: 3.0488 - output_2_loss: 2.8657 - output_3_loss: 32.2687 - output_4_loss: 32.2558WARNING:tensorflow:Gradients do not exist for variables ['qa_net/highway0_gate/bias:0', 'qa_net/highway0_linear/bias:0', 'qa_net/multi_head_attention/bias:0', 'qa_net/multi_head_attention_1/bias:0'] when minimizing the loss.


894/894 [==============================] - 365s 408ms/step


100%|████████████████████████████████████████████████████████████████████████| 10570/10570 [00:23<00:00, 459.11it/s]


{
  "exact": 27.80510879848628,
  "f1": 38.38610877686326,
  "total": 10570,
  "HasAns_exact": 27.80510879848628,
  "HasAns_f1": 38.38610877686326,
  "HasAns_total": 10570
}
Model: "qa_net"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
batch_slice (BatchSlice)     multiple                  0         
_________________________________________________________________
batch_slice_1 (BatchSlice)   multiple                  0         
_________________________________________________________________
qa_output (OutputLayer)      multiple                  0         
_________________________________________________________________
depthwise_conv (DepthwiseCon multiple                  17408     
_________________________________________________________________
depthwise_conv_1 (DepthwiseC multiple                  17152     
_________________________________________________________________
word_embedding (Em

In [5]:
!sudo apt-get install tree
!tree ./ >> README.md